In [62]:
import pandas as pd
import numpy as np
import requests
import folium

In [63]:
# Create a JSON request for the API
# This is the data we want to get from the API
northeastern_coordinate = "-71.09033,42.33976;"
coordinate_string = '-71.2038948,42.4299758;-71.1060828,42.3511927;-71.0969274,42.3446263;-71.130887,42.35304;-71.1459593,42.3501823;-71.1460435,42.3495825;-71.1217152,42.3426377;-71.1258765,42.331864;-71.1095021,42.3364675;-71.133103,42.3890049;-71.0851891,42.3500031;-71.1123834,42.3360385;-71.2273649,42.3145041;-71.0834061,42.341987;-71.0992038,42.3306454;-71.0990577,42.3381442;-71.0949218,42.3419564;-71.0942861,42.3413301;-71.0908104,42.329969;-71.0913583,42.3490205;-71.1000217,42.3323776;-71.1241295,42.3518397;-71.1618052,42.3245965;-71.1625829,42.340795;-71.167854,42.4107892;-71.155555,42.3317473;-71.1227278,42.3965778;-71.3598149,42.3140229;-71.1126695,42.3836229;-71.119149,42.3884;-71.0872846,42.2961434;-71.1427371,42.3433772;-71.1438455,42.3569102;-71.1313443,42.3525708;-71.1284677,42.3631904;-71.119301,42.388547;-71.097883,42.381008;-71.1107166,42.3741209;-71.1194344,42.3754427;-71.1013044,42.3627462;-71.1108423,42.3838224;-71.1026937,42.3820702;-71.1189467,42.373465;-71.1208817,42.3732344;-71.0968274,42.3799095;-71.094048,42.339381;-71.1854722,42.3621177;-71.1146697,42.3782386;-71.0935443,42.3817274;-71.0906355,42.3616095;-71.1161887,42.3766442;-71.0962734,42.3627993;-71.1155576,42.3784629;-71.0949101,42.3797674;-71.1087411,42.3640287;-71.09476,42.37736;-71.1014951,42.3614115;-71.1024769,42.3822934;-71.1011111,42.3636597;-71.0898829,42.3463992;-71.0983169,42.3319001;-71.0945712,42.3253252;-71.1122037,42.4008442'
coordinates = requests.get('http://acetyl.net:5000/trip/v1/bike/' + northeastern_coordinate + coordinate_string)

coordinates = coordinates.json()

In [64]:
# Create a dataframe from the JSON
df = pd.DataFrame(coordinates['waypoints'])

In [65]:
# Separate the location column into lon and lat columns
df['lat'] = df['location'].apply(lambda x: x[0])
df['lon'] = df['location'].apply(lambda x: x[1])

df['waypoint_index'] = df['waypoint_index'].astype(int)

# Map out the waypoints in order of the waypoint index
df = df.sort_values(by=['waypoint_index'])

In [66]:
df

waypoint_index  trips_index  \
0                0            0   
14               1            0   
60               2            0   
46               3            0   
16               4            0   
..             ...          ...   
61              59            0   
15              60            0   
19              61            0   
31              62            0   
62              63            0   

                                                 hint   distance  \
0   DoUhgBeFIYCcAAAAJgAAAAAAAAARAAAAm0CKQdkZiEAAAA...   0.236958   
14  lhgDgIkYA4BkAAAAIgEAAFoBAAAaAAAAJyAzQWNrAEI8Ax...   7.134933   
60  tg0igLoNIoAOAAAAAAAAADwAAADtAQAA8CrBQAAAAACcrM...  17.496916   
46  k4chgBiIIYAKAAAAFwAAAPQDAAB_AgAAHn2aP-biHUBi6e...  36.240351   
16  rLwhgLG8IYAEAAAABQAAADAAAABsAAAA1X8CQHGb7D9Kz6...  24.054372   
..                                                ...        ...   
61  g38hgI1_IYBOAAAAfwAAAAAAAAAAAAAAZ4ECQsbEUkIAAA...  12.789906   
15  cX8hgJF_IYA1AAAAMAAAAGcAAABOAAAATyWxQQ77nUEHMC...  22.776295   
19  5tYhgJHXIYAIAAAArQAAADwAAABCAQAAaRlbQD16mUGpAc...  17.374491   
31  WhEngAASJ4BcAAAAdwAAAHoBAAAFAAAAI3gkQQlZRUJLNi...  13.907079   
62  s9QhgLbUIYAwAAAAkAAAAAAAAAAAAAAA2XmpQNgrgEEAAA...   4.111715   

                      name                 location        lat        lon  
0   Northeastern (Inbound)  [-71.090331, 42.339762] -71.090331  42.339762  
14                           [-71.083465, 42.34194] -71.083465  42.341940  
60        Public Alley 901  [-71.089677, 42.346361] -71.089677  42.346361  
46                          [-71.093834, 42.339096] -71.093834  42.339096  
16                          [-71.099284, 42.338007] -71.099284  42.338007  
..                     ...                      ...        ...        ...  
61          Tremont Street  [-71.098267, 42.332009] -71.098267  42.332009  
15        Alleghany Street   [-71.099348, 42.33047] -71.099348  42.330470  
19           Dudley Street  [-71.090904, 42.329829] -71.090904  42.329829  
31        Blue Hill Avenue  [-71.087449, 42.296172] -71.087449  42.296172  
62                           [-71.09454, 42.325354] -71.094540  42.325354  

[64 rows x 8 columns]

In [67]:
# Create a map
m = folium.Map(location=[df['lon'].mean(), df['lat'].mean()], zoom_start=11)

# Add a marker for each waypoint and connect with a line as the salesman would travel
for i in range(len(df)):
    folium.Marker([df.iloc[i]['lon'], df.iloc[i]['lat']], popup=df.iloc[i]['name']).add_to(m)
    if i < len(df) - 1:
        folium.PolyLine([[df.iloc[i]['lon'], df.iloc[i]['lat']], [df.iloc[i + 1]['lon'], df.iloc[i + 1]['lat']]],
                        color="red", weight=2.5, opacity=1).add_to(m)

# Display the map
m

In [68]:
trip_hrs = int(coordinates['trips'][0]['duration'])/3600
print("The trip will take {} hours".format(trip_hrs))

The trip will take 10.198055555555555 hours
